# Sistema de Compressão

$ \frac{d\dot{m}}{dt} = \frac{A_1}{L_C}(\phi (N(t), \dot{m})P_1 - P_P(t)) $

$ \frac{d P_P}{dt} = \frac{C_1^2}{\nu _P}(\dot{m}(t) - \alpha (t) K_\nu \sqrt{P_P - P_{out}}) $

$ \begin{matrix} A_1 & = & 2.6\centerdot 10^{-3} m² \\
\nu _P & = & 2.0 m³ \\
L_C & = & 2.0 m \\
K_\nu & = & \frac{0.38 kg}{(kPa)^{0.5}s} \\
P_1 & = & 4.5 MPa \\
P{out} & = & 5.0 MPa \end{matrix}
$

$ \frac{d\dot{m}}{dt} = \frac{2.6\centerdot 10^{-3}}{2.0}(\phi (N(t), \dot{m})\centerdot 4.5 - P_P) $

$ \frac{d P_P}{dt} = \frac{479.029^2}{2.0}(\dot{m} - \alpha {0.38} \sqrt{P_P - 5.0}) $

#### Importações

In [1]:
import numpy as np
from scipy.optimize import fsolve
import casadi as ca
import plotly.graph_objects as go
import optuna
from plotly.subplots import make_subplots
import time
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset
import pandas as pd
from scipy.interpolate import griddata
from libs.simulationn import Simulation
from libs.Model import MyModel
from libs.Interpolation import Interpolation

/home/matheus/.local/lib/python3.12/site-packages/matplotlib/projections/__init__.py:63: UserWarning: Unable to import Axes3D. This may be due to multiple versions of Matplotlib being installed (e.g. as a system package and as a pip package). As a result, the 3D projection is not available.
  warnings.warn("Unable to import Axes3D. This may be due to multiple versions of "


#### Constantes e Variáveis Auxiliares

In [22]:
np.random.seed(42)
print(np.random.seed)

# Constantes
A1 = (2.6)*(10**-3)
Lc = 2
kv = 0.38
P1 = 4.5
P_out = 5
C = 479

timestep = 3 # Passos no passado para prever o próximo
nAlphas = 30 # Número de vezes que o Alfa irá mudar, considere o treino e os testes.
alphas = np.random.uniform(0.35,0.65, nAlphas+1) # Abertura da válvula
N_RotS = np.random.uniform(27e3, 5e4, nAlphas+1)
epochs = 1000
nData = 800
nAlphasTeste = 7
nDataTeste = nData//nAlphasTeste
perturb = 1e-4
tempo = 80
tempoTeste = 60
dt = 0.1 # Tempo amostral

# Variáveis auxiliares
interval = [np.linspace(i * tempo, (i + 1) * tempo, nData) for i in range(nAlphas)]
interval_test = [np.linspace(i * tempoTeste, (i + 1) * tempoTeste, nDataTeste) for i in range(nAlphasTeste)]
massFlowrate = []
PlenumPressure = []
alpha_values = []
RNN_train = []
RNN_trainFut = []

<built-in function seed>


##### Cálculo da Solução

In [23]:
lut = Interpolation('./tabela_phi.csv')
lut.load_data()
interpolation = lut.interpolate()
sim = Simulation(A1, Lc, kv, P1, P_out, C, alphas, N_RotS, nAlphas, nData, perturb, tempo, dt, interpolation, timestep)
# Execute a simulação
sim.run()

massFlowrate = sim.massFlowrate
PlenumPressure = sim.PlenumPressure
alpha_values = sim.alpha_values
phi_values = sim.Phi_values
x_min = sim.x_min
x_max = sim.x_max
X_train = sim.X_train
y_train = sim.y_train

print(sim.time)

11.072815418243408


##### Gráfico do Modelo

In [24]:
fig = make_subplots(rows=2, cols=2, subplot_titles=("Vazão vs Tempo", "Pressão vs Tempo", "Alpha vs Tempo", "Phi vs Tempo"))

for i in range(0, nAlphas):
    # Vazão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(massFlowrate[i]), mode='lines',
                             name='Vazão', legendgroup='massflow', showlegend=i == 0), row = 1, col = 1)
    # Pressão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(PlenumPressure[i]), mode='lines',
                             name='Pressão', legendgroup='pressure', showlegend=i == 0), row = 1, col = 2)
    # Alphas
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(alpha_values[i]), mode='lines', 
                             name='Alphas', line=dict(dash='dash'), legendgroup='alpha', showlegend=i == 0), row = 2, col = 1)
    # Phi
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(phi_values[i]), mode='lines', 
                             name='Alphas', line=dict(dash='dash'), legendgroup='alpha', showlegend=i == 0), row = 2, col = 2)

# Atualiza layout
fig.update_layout(
    xaxis_title='Tempo',
    grid=dict(rows=1, columns=3),
    template='plotly',
    showlegend=False,
    height = 600
)

# Mostra a figura
fig.show()


### Rede Neural

##### Dados de Treino

In [25]:
import optuna
from torch.utils.data import DataLoader

def objective(trial):
    # Definir os hiperparâmetros a serem otimizados
    units = trial.suggest_int("units", 10, 100, step=10)
    batch_size = trial.suggest_categorical("batch_size", [16, 32, 64, 128])
    lr = 1e-5
    
    # Criar o modelo com o número de neurônios sugerido
    model = MyModel(units, A1, Lc, kv, P1, P_out, C, dt, x_min, x_max, interpolation)
    
    # Configurar o DataLoader com o batch_size sugerido
    train_dataset = TensorDataset(X_train, y_train)
    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    
    # Configurar o otimizador com a taxa de aprendizado sugerida
    optimizer = optim.Adam(model.parameters(), lr=lr)
    
    # Treinamento
    model.train()
    epochs = 100  # Escolha o número de épocas desejado para avaliação
    for epoch in range(epochs):
        total_loss = 0
        for inputs, y_true in train_loader:
            optimizer.zero_grad()
            y_pred = model(inputs)
            loss = model.loss_custom(y_true, y_pred, inputs)
            loss.backward()
            optimizer.step()
            total_loss += loss.item()
    
    # Retornar o valor médio da perda como métrica de avaliação
    return total_loss / len(train_loader)

# Criar o estudo Optuna
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=10)

# Resultados
print("Best trial:")
print(f"  Units: {study.best_params['units']}")
print(f"  Batch size: {study.best_params['batch_size']}")

[I 2024-12-07 15:38:59,705] A new study created in memory with name: no-name-3d0316e2-dbe0-4fc5-8932-4abd71f1ad1c
[W 2024-12-07 15:39:00,989] Trial 0 failed with parameters: {'units': 90, 'batch_size': 128} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "/usr/local/lib/python3.12/dist-packages/optuna/study/_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
                      ^^^^^^^^^^^
  File "/tmp/ipykernel_5154/1651462402.py", line 27, in objective
    y_pred = model(inputs)
             ^^^^^^^^^^^^^
  File "/home/matheus/.local/lib/python3.12/site-packages/torch/nn/modules/module.py", line 1553, in _wrapped_call_impl
    return self._call_impl(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/matheus/.local/lib/python3.12/site-packages/torch/nn/modules/module.py", line 1562, in _call_impl
    return forward_call(*args, **kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/m

KeyboardInterrupt: 

##### Treinamento

In [27]:
model = MyModel(60, A1, Lc, kv, P1, P_out, C, dt, x_min, x_max, interpolation)

train_dataset = TensorDataset(X_train, y_train)
train_loader = DataLoader(train_dataset, batch_size= 64, shuffle=True)
Adam = optim.Adam
model.train_model(model, train_loader, 1e-6 , 5000, Adam)

Epoch [1/5000], Loss: 754.043302734375
Epoch [2/5000], Loss: 744.0993396809896
Epoch [3/5000], Loss: 734.283212890625
Epoch [4/5000], Loss: 724.5810022786459
Epoch [5/5000], Loss: 714.968949625651
Epoch [6/5000], Loss: 705.4116336263021
Epoch [7/5000], Loss: 695.9075236002604
Epoch [8/5000], Loss: 686.4248128255208
Epoch [9/5000], Loss: 676.9367415364584
Epoch [10/5000], Loss: 667.4594946289062
Epoch [11/5000], Loss: 657.9606458333334
Epoch [12/5000], Loss: 648.4381538899739
Epoch [13/5000], Loss: 638.8751101888021
Epoch [14/5000], Loss: 629.2603880208334
Epoch [15/5000], Loss: 619.6050710449218
Epoch [16/5000], Loss: 609.8989822591146
Epoch [17/5000], Loss: 600.1316678059895
Epoch [18/5000], Loss: 590.3223727213542
Epoch [19/5000], Loss: 580.4266402994791
Epoch [20/5000], Loss: 570.4711520996094
Epoch [21/5000], Loss: 560.4462811686197
Epoch [22/5000], Loss: 550.345488688151
Epoch [23/5000], Loss: 540.1869136555989
Epoch [24/5000], Loss: 529.9736436360677
Epoch [25/5000], Loss: 519.71

##### Dados de teste

In [36]:
massFlowrateTeste = []
PlenumPressureTeste = []
RNN_test = []
x_test = []
alpha_valuesTeste = []
aux1 = []
aux2 = []
alphasTeste = np.random.uniform(0.35,0.65, nAlphasTeste) # Abertura da válvula
N_RotSTeste = np.random.uniform(27e3, 5e4, nAlphasTeste+1)

sim = Simulation(A1, Lc, kv, P1, P_out, C, alphasTeste,N_RotSTeste, nAlphasTeste, nDataTeste, perturb, tempoTeste, dt, interpolation, timestep)

sim.run()

massFlowrateTeste = sim.massFlowrate
PlenumPressureTeste = sim.PlenumPressure
alpha_valuesTeste = sim.alpha_values
x_test = sim.X_train
print(sim.time)


massFlowrateTeste = np.array(massFlowrateTeste)
PlenumPressureTeste = np.array(PlenumPressureTeste)
interval3 = np.linspace(0, tempoTeste*nAlphasTeste, len(x_test))

0.4207947254180908


##### Gráfico Rede Neural

In [37]:
fig = make_subplots(rows=1, cols=2, subplot_titles=("Mass Flow Rate vs Time", "Plenum Pressure vs Time"))

tm1 = time.time()
# Colocando o modelo em modo de avaliação

# Supondo que x_test já esteja definido e seja um tensor PyTorch
with torch.no_grad():  
    prediction = model(x_test)

mass = prediction[:, :, 0]
pressure = prediction[:, :, 1]

mass = mass.detach().numpy()
pressure = pressure.detach().numpy()

tm2 = time.time()
print(tm2-tm1)

fig.add_trace(go.Scatter(x=interval3,y=np.squeeze(mass),mode='lines',
                                line=dict(dash='solid')),row=1, col=1)
fig.add_trace(go.Scatter(x=interval3,y=np.squeeze(pressure),mode='lines',
                                line=dict(dash='solid')),row=1, col=2)


for i in range(nAlphasTeste):
    # Modelo
    fig.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(massFlowrateTeste[i]), mode='lines',name='Model Mass Flow Rate', line=dict(dash='dash', color='red')),
                  row=1, col=1)
    fig.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(PlenumPressureTeste[i]), mode='lines', name= 'Model Plenum Pressure', line=dict(dash='dash', color='red')),
                  row=1, col=2)

fig.update_layout(
    title='Resultados Rede Neural',
    xaxis_title='Time',
    yaxis_title='Value',
    template='plotly',
    showlegend=False
)
fig.show()


0.004965782165527344


In [38]:
massFlowrate100, PlenumPressure100,time2 = model.test_model(x_test, interval3, model)
print(time2)

torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size([1, 3, 4])
torch.Size

In [39]:
fig3 = make_subplots(rows=1, cols=2, subplot_titles=("Mass Flow Rate vs Time", "Plenum Pressure vs Time"))

fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(massFlowrate100),mode='lines',
                                line=dict(dash='solid')),row=1, col=1)
fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(PlenumPressure100),mode='lines',
                                line=dict(dash='solid')),row=1, col=2)

for i in range(nAlphasTeste):
    # Modelo
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(massFlowrateTeste[i]), mode='lines',name='Model Mass Flow Rate', line=dict(dash='dash', color='red')),
                  row=1, col=1)
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(PlenumPressureTeste[i]), mode='lines', name= 'Model Plenum Pressure', line=dict(dash='dash', color='red')),
                  row=1, col=2)

fig3.update_layout(
    title='Resultados Rede Neural',
    xaxis_title='Time',
    yaxis_title='Value',
    template='plotly',
    showlegend=False
)
fig3.show()